# Integration of Recommendation and Process Mining

In [1]:
import numpy as np
import pandas as pd
from collections import Counter
import pm4py
from datetime import timedelta, date
import random

# Recommendation

In [13]:
df = pd.read_csv("Electronics_Review.csv")
df.head()

Unnamed: 0 marketplace  customer_id       review_id  product_id  \
0           0          US       179886   RY01SAV7HZ8QO  B00NTI0CQ2   
1           1          US     37293769  R1XX8SDGJ4MZ4L  B00BUCLVZU   
2           2          US      8332121  R149Q3B5L33NN5  B00RBX9D5W   
3           3          US     47054962  R2ZVD69Z6KPJ4O  B00UJ3IULO   
4           4          US     23413911  R1DIKG2G33ZLNP  B0037UCTXG   

   product_parent                                      product_title  \
0       667358431  Aketek 1080P LED Protable Projector HD PC AV V...   
1       621695622             TiVo Mini with IR Remote (Old Version)   
2       143071132  Apple TV MD199LL/A Bundle including remote and...   
3       567816707             New Roku 3 6.5 Foot HDMI - Bundle - v1   
4       909557698  Generic DVI-I Dual-Link (M) to 15-Pin VGA (F) ...   

     product_category  star_rating  helpful_votes  total_votes vine  \
0  Home Entertainment            4              0            0    N   
1  Home Entertainment            5              0            0    N   
2  Home Entertainment            5              0            0    N   
3  Home Entertainment            1              0            2    N   
4  Home Entertainment            4              0            0    N   

  verified_purchase                              review_headline  \
0                 Y                   good enough for my purpose   
1                 N  Tell the Cable Company to Keep their Boxes!   
2                 Y                             Works perfectly!   
3                 Y  It doesn't work. Each time I try to use ...   
4                 Y                                  As pictured   

                                         review_body review_date  
0  not the best picture quality but surely suitab...  2015-08-31  
1  Not only do my TiVo Minis replace the boxes th...  2015-08-31  
2               Works perfectly! Very user friendly!  2015-08-31  
3  It doesn't work. Each time I try to use it, th...  2015-08-31  
4  I received the item pictured.  I am unsure why...  2015-08-31

In [14]:
dfd = df
dfd = dfd.sort_values(by = 'review_date',ascending=True)
dfd.head()

Unnamed: 0 marketplace  customer_id       review_id  product_id  \
705486      705486          US     51191371   RVV912AL3TXDP  B000006TJP   
705485      705485          US     51775511  R1QCR0Q06G5NZF  B00000J4GI   
705484      705484          US     52316356  R21FKOCDP1WD2S  B00000JFMK   
705480      705480          US     52865215  R2P4RWJWI1XR8H  B00000JFMK   
705483      705483          US     53048056  R1RDKIWUZQM7GJ  B00000JFMK   

        product_parent                          product_title  \
705486       750329544         1 In 21 - A Tupac Shakur Story   
705485       150762671               JVC XV-D701BK DVD Player   
705484       893744918  Panasonic DVD-L50 Portable DVD Player   
705480       893744918  Panasonic DVD-L50 Portable DVD Player   
705483       893744918  Panasonic DVD-L50 Portable DVD Player   

          product_category  star_rating  helpful_votes  total_votes vine  \
705486  Home Entertainment            5              1            1    N   
705485  Home Entertainment            3              2           21    N   
705484  Home Entertainment            4              0            0    N   
705480  Home Entertainment            5              0            0    N   
705483  Home Entertainment            5              0            0    N   

       verified_purchase                                    review_headline  \
705486                 N  Gets in your blood and really relieves your so...   
705485                 N       One Con they don't tell you about...........   
705484                 N                            Excellent Expensive Toy   
705480                 N    Awesome toy  that can be hooked up to anything.   
705483                 N                        It's a great little gadget!   

                                              review_body review_date  
705486  2Pac is an amazing artist.  He uses his life e...  1998-10-15  
705485  Before you venture out into the DVD world, you...  1999-06-09  
705484  Picture quality is fantastic.  Lots of fun to ...  1999-06-12  
705480  Great picture, awesome toy to bring for travel...  1999-06-14  
705483  We love ours.  You can take it with you on tri...  1999-06-14

In [4]:
ld = pd.read_csv("logs_52340667.csv")
ld.head()

Unnamed: 0  time_stamp                                        log_strings
0           0  2011-04-20                     google-low budget portable TVs
1           1  2011-04-21                   youtube-panasonic 32 inch review
2           2  2011-04-22        youtube-compare quality of 7inch and 32inch
3           3  2011-04-23  google-price comparision between panasonic and...
4           4  2011-04-24                                google-portable TVs

In [5]:
searchdata = ld['log_strings'].tolist()
s = ''
for d in searchdata:
    s = s+" "+d
print(s)

 google-low budget portable TVs youtube-panasonic 32 inch review youtube-compare quality of 7inch and 32inch google-price comparision between panasonic and tivax google-portable TVs amazon-32 inch tv youtube-compare quality of 7inch and 32inch amazon-32 inch tv amazon-digital portable 7 inch tvs amazon-digital portable 7 inch tvs youtube-compare quality of 7inch and 32inch google-price comparision between panasonic and tivax google-portable TVs youtube-compare quality of 7inch and 32inch amazon-digital portable 7 inch tvs google-low budget portable TVs google-portable TVs google-portable TVs youtube-panasonic 32 inch review amazon-32 inch tv google-low budget portable TVs amazon-32 inch tv amazon-digital portable 7 inch tvs amazon-32 inch tv flipkart-poratble tv youtube-compare quality of 7inch and 32inch google-price comparision between panasonic and tivax amazon-digital portable 7 inch tvs


In [6]:
def remov_duplicates(input): 
    input = input.split(" ") 
    for i in range(0, len(input)): 
        input[i] = "".join(input[i]) 
    UniqW = Counter(input) 
    stringu = " ".join(UniqW.keys())
    return stringu

In [7]:
se = remov_duplicates(s)
print(se)

 google-low budget portable TVs youtube-panasonic 32 inch review youtube-compare quality of 7inch and 32inch google-price comparision between panasonic tivax google-portable amazon-32 tv amazon-digital 7 tvs flipkart-poratble


In [8]:
se = se.replace('-',' ')
se

' google low budget portable TVs youtube panasonic 32 inch review youtube compare quality of 7inch and 32inch google price comparision between panasonic tivax google portable amazon 32 tv amazon digital 7 tvs flipkart poratble'

In [9]:
li = ['google','amazon','youtube','flipkart'] #removing website names
for i in li:
    se = se.replace(i,'')
se

'  low budget portable TVs  panasonic 32 inch review  compare quality of 7inch and 32inch  price comparision between panasonic tivax  portable  32 tv  digital 7 tvs  poratble'

In [10]:
ls = ['compare','comparision','between','review','and']
for i in ls:
    se = se.replace(i,'')
se

'  low budget portable TVs  panasonic 32 inch    quality of 7inch  32inch  price   panasonic tivax  portable  32 tv  digital 7 tvs  poratble'

In [11]:
se = se.lower()
se = remov_duplicates(se)
print(se)

 low budget portable tvs panasonic 32 inch quality of 7inch 32inch price tivax tv digital 7 poratble


In [12]:
finstr = se.split()
finstr

['low',
 'budget',
 'portable',
 'tvs',
 'panasonic',
 '32',
 'inch',
 'quality',
 'of',
 '7inch',
 '32inch',
 'price',
 'tivax',
 'tv',
 'digital',
 '7',
 'poratble']

In [16]:
itemsinrev = df['product_title'].tolist()
itemsinrev

['Aketek 1080P LED Protable Projector HD PC AV VGA USB HDMI(Black)',
 'TiVo Mini with IR Remote (Old Version)',
 'Apple TV MD199LL/A Bundle including remote and High-Speed HDMI Cable (6 Feet) (Current Version) (Certified Refurbished)',
 'New Roku 3 6.5 Foot HDMI - Bundle - v1',
 'Generic DVI-I Dual-Link (M) to 15-Pin VGA (F) Adapter',
 'Samsung 3D LED HDTV (Silver)',
 'Jiake Wireless Bluetooth A2DP Stereo Music Headset Universal Vibration Neckband Style HBS-700 Earphone for Mobile Phones / Samsung Galaxy S4 S5 Note 2 3 / Lg G2 Pro / HTC ONE M7 M8 / Moto X G / Google Nexus 4 5 / Nokia Lumia 1520 1020 /Sony Xperia Z2 Z1 L39h / Iphone 5s 5c / Ipad Air (black)',
 '3pcs/lot 3in1 3ft 6ft 2m 10ft Extra Long Noodle Flat USB Charger Cable Cords for Iphone 4 4s Ipod Touch 4 Nano 6 (hotpink)',
 'Matricom G-Box Q² Android TV Streaming Media Mini PC [2GB/16GB/4K] Quad/Octo Core',
 'VIZIO S2920W-C0B 29" 2.0 High Definition Sound Bar with Bluetooth (Refurbished)',
 'Hitachi 49" Class 1080p LED HDTV -

In [17]:
def Remove(duplicate): 
    return list(dict.fromkeys(duplicate))

In [18]:
allitems = Remove(itemsinrev)

In [19]:
len(allitems)

42925

In [36]:
rates = []
for item in finitems:
    litem = item.lower()
    subitem = litem.split()
    it = 0
    for sub in finstr:
        if sub in subitem:
            it = it+1
    rates.append(it)
    print(it)

0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0


0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0


0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0


0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0


0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0


...

0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0


0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0


1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0


0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2


0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
1
0
0
0
0
0
0
1
0
0
0
0
0
0
0
0
0
1
0
0
0
0
0
0
0
1
0
0
0
0
0
0
0
1
0
0
0
0
0
0
0
0
0
0
0
0
0
1
1
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
1
0
0
0
0
0
0
0
0
1
1
0
0
0
0
0
0
0
0
1
0
0
0
1
0
0
0
0
0
0
0
0
0
0


tem = item.split()
    it = 0
    for sub in finstr:
        if sub in tem:
            it = it+1
    rates.append(it)
    print(it)

In [25]:
cid = df["customer_id"].tolist()
cid = Remove(cid)
len(cid)

609764

In [26]:
cid.remove(52340667)

In [27]:
userid = 52340667

userRatings = df[df['customer_id'] == userid]
loved = userRatings[userRatings['star_rating'] >= 4]
hated = userRatings[userRatings['star_rating'] <= 3]
recitem = []
love = loved[:-1]
for i in cid:
    tempt = df[df['customer_id'] == i]
    temlis = tempt['product_parent'].tolist()
    for item in love['product_parent']:
        if item in temlis:
            indexit = temlis.index(item)
            if len(temlis) > indexit+1 :
                print(temlis[indexit:])
                recitem = recitem + temlis[indexit:]
recitemsorder = [item for items, c in Counter(recitem).most_common() for item in [items]]
itemstorec = recitemsorder
for item in itemstorec:
    if item in hated:
        del itemstorec[itemstorec.index(item)]
finitems = []
for num in itemstorec:
    finitems = finitems + df[df['product_parent'] == num]['product_title'].tolist()

[116329024, 602517876, 437478031, 621024737, 155939910, 638696361, 129909303, 207746434, 44332148, 177514197, 150097560, 537458312]
[437478031, 621024737, 155939910, 638696361, 129909303, 207746434, 44332148, 177514197, 150097560, 537458312]
[207746434, 44332148, 177514197, 150097560, 537458312]
[106680162, 838854155]
[106680162, 838854155]
[247626852, 629020148]
[120948267, 788108393, 686623255]
[788108393, 686623255]
[247626852, 257363054, 420330031, 821353052]
[264003817, 611127351]
[936769453, 765911483, 793325723, 129909303, 136883677, 842139965, 187130118, 897454931, 218285193, 739845672, 956801336, 897454931, 964922399, 685593182]
[842139965, 187130118, 897454931, 218285193, 739845672, 956801336, 897454931, 964922399, 685593182]
[828072002, 295978861, 419158136, 482128274, 129909303, 545952702, 489148814, 151743886, 142881343, 653068098, 362286013, 681384432, 611127351, 997486664, 858363416, 282530080, 234623897, 361049841, 878751094]
[482128274, 129909303, 545952702, 489148814,

[984700493, 848771863, 562633680]
[478174861, 325657500, 521976969, 754791093, 621695622]
[207746434, 796862845, 825888938]
[478174861, 106680162, 442239993]
[106680162, 442239993]
[106680162, 442239993]
[207746434, 382551044, 170467798]
[207746434, 682337057]
[545952702, 207746434]
[207746434, 207746434, 565314198]
[545952702, 652493414, 920848599, 925731090, 986027941, 558782160, 496798322, 149901035]
[207746434, 858363416, 754791093]
[712501277, 924863849]
[7975759, 482128274]
[842139965, 343185803]
[545952702, 512145979]
[762492573, 675906263]
[545952702, 289436200]
[712501277, 181459790, 278516208]
[545952702, 545952702]
[7975759, 902956362]
[842139965, 557449873, 416210710, 820971376, 182475624, 624249492, 851224649, 625345159, 662598191, 496798322, 990680505]
[207746434, 739845672]
[920622410, 287248334]
[153135896, 37858553]
[182626797, 588138789, 576095495, 90550683]
[207746434, 741973356, 529874821, 940063681]
[478174861, 37054460]
[207746434, 69584855]
[712501277, 711713824,

[741798439, 319886506]
[118053924, 174291292]
[118053924, 174291292]
[118053924, 93905937]
[118053924, 93905937]
[741798439, 432145172]
[741798439, 727509453]
[106680162, 343185803, 219655965]
[106680162, 343185803, 219655965]
[106680162, 118053924]
[106680162, 118053924]
[940063681, 104498493]
[118053924, 191212573, 521976969]
[118053924, 191212573, 521976969]
[106680162, 343185803, 58908028]
[106680162, 343185803, 58908028]
[984700493, 820971376, 827244053, 219655965, 239364200]
[118053924, 819792667]
[118053924, 819792667]
[57007989, 35905260, 318576328]
[478174861, 326152515, 875886800, 373737286]
[106680162, 868459437]
[106680162, 868459437]
[106680162, 276547250]
[106680162, 276547250]
[118053924, 459782052, 171244366]
[118053924, 459782052, 171244366]
[106680162, 957246369]
[106680162, 957246369]
[106680162, 268883996, 332919308]
[106680162, 268883996, 332919308]
[964994771, 495746847, 28498132]
[964994771, 495746847, 28498132]
[788108393, 539418830, 192359474]
[199030523, 98142

[478174861, 203936195]
[106680162, 753754497]
[106680162, 753754497]
[821353052, 831589543]
[762492573, 584839158]
[106680162, 726240806, 643958402]
[106680162, 726240806, 643958402]
[380032617, 314400887]
[106680162, 711713824]
[106680162, 711713824]
[106680162, 761928784]
[106680162, 761928784]
[106680162, 492999563]
[106680162, 492999563]
[569952701, 985480409]
[478174861, 99907853, 697730172]
[106680162, 65574971, 219655965]
[106680162, 65574971, 219655965]
[842425489, 92981122, 105752981, 333015736]
[144717794, 434172006, 360741378, 80781849, 31827757]
[247626852, 64277441]
[842425489, 986427485]
[821353052, 902956362, 134207981, 490188033, 820191596, 819932318, 208303699, 189633573, 682337057, 806432372]
[821353052, 61796757, 961435889, 634766915]
[106680162, 559358706]
[106680162, 559358706]
[106680162, 597788971]
[106680162, 597788971]
[106680162, 189633573]
[106680162, 189633573]
[741798439, 841657152]
[106680162, 477570079, 509903985, 640842183, 294276048, 62489178, 401834922

[821353052, 997486664]
[437562107, 781336599]
[545952702, 453950718]
[788108393, 470568705, 61796757, 200581519]
[821353052, 479110801, 591435204]
[821353052, 380345682]
[821353052, 246040695, 537939183, 962317283]
[793386394, 71869363]
[821353052, 173984571]
[821353052, 746116610, 783661249, 599641152, 219655965, 177157370, 661150531, 962211121]
[118053924, 702676553, 521976969, 820971376, 208303699]
[118053924, 702676553, 521976969, 820971376, 208303699]
[821353052, 47895751, 864030234, 429064020, 804927280, 629020148, 786982622, 342175982, 984826040, 99277561, 902057748]
[793386394, 962211121]
[821353052, 411838756]
[118053924, 696986746, 43838262]
[118053924, 696986746, 43838262]
[437562107, 179067821, 440451150, 323609361, 152018143, 271566382, 300134285, 606996649, 303107223]
[106680162, 709560176]
[106680162, 709560176]
[437562107, 963311490, 219655965, 761876214, 761876214]
[437562107, 923262797]
[437562107, 557213720]
[437562107, 815674058]
[437562107, 196181514, 144704512]
[4

[821353052, 711615099]
[933448658, 147708531, 511941195, 101178538, 241595152, 681704590]
[821353052, 502663471]
[106680162, 561286608]
[106680162, 561286608]
[478174861, 211081321]
[821353052, 471820675, 746116610]
[975344982, 868028026]
[821353052, 591435204, 989813046]
[821353052, 98796673]
[842425489, 850684326]
[821353052, 343185803]
[437562107, 984046704]
[821353052, 770125576]
[964994771, 768156927]
[964994771, 768156927]
[120948267, 761876214]
[437562107, 192019811]
[106680162, 162735440]
[106680162, 162735440]
[437562107, 611127351]
[821353052, 359786047]
[821353052, 821353052]
[569952701, 343185803]
[821353052, 606996649]
[821353052, 968573851, 944360307, 730788520]
[118053924, 895402190]
[118053924, 895402190]
[106680162, 359786047]
[106680162, 359786047]
[821353052, 535227482, 255487074]
[106680162, 139129158]
[106680162, 139129158]
[821353052, 129909303]
[821353052, 757458213, 215324268, 134207981]
[964994771, 67673718]
[964994771, 67673718]
[821353052, 104243794]
[8213530

In [48]:
finitems

items  rank
0       Philips DVP642 DivX-Certified Progressive-Scan...     0
198648            Samsung LNT4661F 46-Inch 1080p LCD HDTV     0
198649            Samsung LNT4661F 46-Inch 1080p LCD HDTV     0
198650            Samsung LNT4661F 46-Inch 1080p LCD HDTV     0
198651            Samsung LNT4661F 46-Inch 1080p LCD HDTV     0
...                                                   ...   ...
313987    Tivax STB-T8 Digital to Analog TV Converter Box     3
313988    Tivax STB-T8 Digital to Analog TV Converter Box     3
313989    Tivax STB-T8 Digital to Analog TV Converter Box     3
313991    Tivax STB-T8 Digital to Analog TV Converter Box     3
314031    Tivax STB-T8 Digital to Analog TV Converter Box     3

[324917 rows x 2 columns]

In [51]:
finalitemsframe = finitems.sort_values(by = 'rank', ascending =False)
finalitemsframe

items  rank
314031    Tivax STB-T8 Digital to Analog TV Converter Box     3
314226    Tivax STB-T8 Digital to Analog TV Converter Box     3
314224    Tivax STB-T8 Digital to Analog TV Converter Box     3
314223    Tivax STB-T8 Digital to Analog TV Converter Box     3
314240    Tivax STB-T8 Digital to Analog TV Converter Box     3
...                                                   ...   ...
233845  Exergen Temporal Artery Thermometer MODEL# 200...     0
233844  Exergen Temporal Artery Thermometer MODEL# 200...     0
233871  Exergen Temporal Artery Thermometer MODEL# 200...     0
233872  Exergen Temporal Artery Thermometer MODEL# 200...     0
13777       Google Chromecast HDMI Streaming Media Player     0

[324917 rows x 2 columns]

itemsinreclis = finalitemsframe[finalitemsframe['rank'] == finalitemsframe['rank'][len(finalitemsframe)-1]]['items'].tolist()

itemsinreclist = Remove(itemsinreclis)

itemsinreclist

In [60]:
finalitemsframe.head()

items  rank
314031  Tivax STB-T8 Digital to Analog TV Converter Box     3
314226  Tivax STB-T8 Digital to Analog TV Converter Box     3
314224  Tivax STB-T8 Digital to Analog TV Converter Box     3
314223  Tivax STB-T8 Digital to Analog TV Converter Box     3
314240  Tivax STB-T8 Digital to Analog TV Converter Box     3

In [ ]:
acout = userRatings['product_title'].tolist()
acoutitem = acout[-1]
print(acoutitem)